In [11]:
# !pip install muon scanpy mofapy2  # se servisse
import os
out_dir = "../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/"
os.makedirs(out_dir, exist_ok=True)

# Config Scanpy
import scanpy as sc
sc.settings.figdir = os.path.join(out_dir, "figures")
os.makedirs(sc.settings.figdir, exist_ok=True)
sc.settings.autoshow = False

In [12]:
import pandas as pd
import numpy as np
import scanpy as sc
import muon as mu
from anndata import AnnData
from sklearn.metrics import adjusted_rand_score
import matplotlib.pyplot as plt

In [13]:
import pandas as pd
import numpy as np
from anndata import AnnData

rna_csv = "../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/gene_expression.csv"
dna_csv = "../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/variant_matrix.csv"

rna_df = pd.read_csv(rna_csv, index_col=0)
dna_df = pd.read_csv(dna_csv, index_col=0)

print(f"RNA shape (genes × cells): {rna_df.shape}")
print(f"DNA shape (variants × cells): {dna_df.shape}")

# Crea AnnData
rna_adata = AnnData(rna_df.T.copy())
dna_adata = AnnData(dna_df.T.copy())

rna_adata.var_names.name = "gene"
dna_adata.var_names.name = "variant"

# Verifica coerenza dei barcode
assert (rna_adata.obs_names == dna_adata.obs_names).all(), "Cell names don't match!"

# === Debug: prime 5×5 celle per ciascuna omica ===
print("\n[DEBUG] Prime 5×5 celle RNA (righe=celle, colonne=geni):")
print(np.round(rna_adata.X[:5, :5], 4))

print("\n[DEBUG] Prime 5×5 celle DNA (righe=celle, colonne=varianti):")
print(np.round(dna_adata.X[:5, :5], 4))

# === Piccolo riassunto dei valori ===
print(f"\n[INFO] RNA — valore medio: {rna_adata.X.mean():.4f}, std: {rna_adata.X.std():.4f}")
print(f"[INFO] DNA — valore medio: {dna_adata.X.mean():.4f}, std: {dna_adata.X.std():.4f}")

RNA shape (genes × cells): (10000, 5000)
DNA shape (variants × cells): (20000, 5000)
[DEBUG] Prime 5×5 celle RNA (righe=celle, colonne=geni):
[[1.5445 0.     3.065  1.8446 2.3458]
 [0.     1.4837 0.     0.     1.6266]
 [1.3126 2.223  4.4167 4.5424 0.    ]
 [5.8761 5.6104 4.0811 0.     4.1624]
 [2.2925 1.86   0.     0.     2.099 ]]

[DEBUG] Prime 5×5 celle DNA (righe=celle, colonne=varianti):
[[0 0 1 0 0]
 [0 0 0 0 0]
 [1 0 1 0 0]
 [0 1 0 0 0]
 [0 0 1 0 0]]
[INFO] RNA — valore medio: 2.1562, std: 1.9827[INFO] DNA — valore medio: 0.1973, std: 0.3979

In [14]:
mdata = mu.MuData({"rna": rna_adata, "dna": dna_adata})
mdata.write(os.path.join(out_dir, "mdata_raw.h5mu"))
print(mdata)

MuData object with n_obs × n_vars = 5000 × 30000
  2 modalities
    rna:	5000 x 10000
    dna:	5000 x 20000

In [15]:
#sc.pp.normalize_total(mdata["rna"])
#sc.pp.log1p(mdata["rna"])
#sc.pp.highly_variable_genes(mdata["rna"], flavor="cell_ranger", n_top_genes=2000)
#mdata.mod["rna"] = mdata["rna"][:, mdata["rna"].var.highly_variable].copy()
sc.pp.scale(mdata["rna"], max_value=10)
sc.tl.pca(mdata["rna"], n_comps=50)
sc.pp.neighbors(mdata["rna"], n_pcs=30)
sc.tl.umap(mdata["rna"])

In [16]:
import numpy as np
import scanpy as sc

# Assicurati che i dati siano binari float
mdata["dna"].X = (mdata["dna"].X > 0).astype(float)

# Filtra varianti troppo rare
sc.pp.filter_genes(mdata["dna"], min_cells=5)

# Filtra varianti troppo frequenti (>95% delle cellule)
to_keep = np.array((mdata["dna"].X.sum(axis=0) < 0.95 * mdata["dna"].n_obs)).flatten()
mdata.mod["dna"] = mdata["dna"][:, to_keep].copy()

# Scala per PCA
sc.pp.scale(mdata["dna"], max_value=10)

# PCA + neighbors + UMAP
sc.tl.pca(mdata["dna"], n_comps=50)
sc.pp.neighbors(mdata["dna"], n_pcs=30)
sc.tl.umap(mdata["dna"])

print("[INFO] Preprocessing DNA binario completato.")

[INFO] Preprocessing DNA binario completato.

In [17]:
import pandas as pd
import os

# Percorso opzionale del file di metadati (modificalo se serve)
meta_csv = "../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/cell_metadata.csv"

true_label_col = None  # nome della colonna con etichetta vera

if os.path.exists(meta_csv):
    print(f"[INFO] Carico metadati da: {meta_csv}")
    metadata = pd.read_csv(meta_csv)

    # Tenta di riconoscere la colonna delle cellule
    if "Cell" in metadata.columns:
        metadata = metadata.set_index("Cell")
    elif "cell_id" in metadata.columns:
        metadata = metadata.set_index("cell_id")
    else:
        print("[WARN] Nessuna colonna 'Cell' trovata nei metadati — controlla il file.")
        print("Colonne disponibili:", metadata.columns.tolist())

    # Aggiungi i metadati alle modalità RNA, DNA e alla vista combinata
    for mod in ["rna", "dna"]:
        mdata.mod[mod].obs = mdata.mod[mod].obs.join(metadata, how="left")
    mdata.obs = mdata.obs.join(metadata, how="left")

    # Cerca possibili colonne che rappresentano la “verità” (label ground truth)
    ct_cols = [c for c in ["TrueCellType", "CellType", "cell_type"] if c in mdata.obs.columns]
    gt_cols = [c for c in ["TrueGenotype", "Genotype", "genotype"] if c in mdata.obs.columns]

    # Combina in una singola colonna "true_label"
    if ct_cols and gt_cols:
        mdata.obs["true_label"] = (
            mdata.obs[ct_cols[0]].astype(str) + "_" + mdata.obs[gt_cols[0]].astype(str)
        )
        true_label_col = "true_label"
        print(f"[INFO] Trovate colonne cell_type ({ct_cols[0]}) e genotype ({gt_cols[0]})")
    elif ct_cols:
        mdata.obs["true_label"] = mdata.obs[ct_cols[0]].astype(str)
        true_label_col = "true_label"
        print(f"[INFO] Trovata colonna cell_type ({ct_cols[0]})")
    elif gt_cols:
        mdata.obs["true_label"] = mdata.obs[gt_cols[0]].astype(str)
        true_label_col = "true_label"
        print(f"[INFO] Trovata colonna genotype ({gt_cols[0]})")
    else:
        print("[WARN] Nessuna colonna adatta trovata per 'true_label'.")

else:
    print(f"[WARN] Nessun file di metadati trovato in {meta_csv}")

print("→ Colonna etichetta vera utilizzata:", true_label_col)

[INFO] Carico metadati da: ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/cell_metadata.csv
[INFO] Trovate colonne cell_type (TrueCellType) e genotype (TrueGenotype)
→ Colonna etichetta vera utilizzata: true_label

In [18]:
# --- BLOCCO 8: Integrazione WNN (RNA+DNA) + UMAP + Leiden + ARI ---

import os
import numpy as np
import pandas as pd
import scanpy as sc
import muon as mu
import matplotlib.pyplot as plt

# Cartelle output (riusa out_dir se già definita, altrimenti usa una di default)
if "out_dir" not in globals():
    out_dir = "./wnn_out/"
os.makedirs(out_dir, exist_ok=True)
fig_dir = os.path.join(out_dir, "figures_wnn")
os.makedirs(fig_dir, exist_ok=True)

# 0) Controlli di base sulle modalità
assert "rna" in mdata.mod and "dna" in mdata.mod, "Mi servono le modalità 'rna' e 'dna' dentro mdata.mod"

print("[INFO] Costruisco grafo multimodale WNN...")
mu.pp.neighbors(mdata, key_added="wnn")   # crea: mdata.uns['wnn'], mdata.obsp['wnn_connectivities'], mdata.obsp['wnn_distances']

# 1) UMAP sul grafo WNN
print("[INFO] Calcolo UMAP su WNN...")
mu.tl.umap(mdata, neighbors_key="wnn")

# Salva anche con un nome esplicito
mdata.obsm["X_wnn_umap"] = mdata.obsm["X_umap"].copy()

# 2) Clustering Leiden su WNN a più risoluzioni
wnn_res_list = [0.5, 1.0, 1.5, 2.0]
print(f"[INFO] Leiden WNN alle risoluzioni: {wnn_res_list}")
for res in wnn_res_list:
    key = f"leiden_wnn_{res}"
    sc.tl.leiden(
        mdata,
        neighbors_key="wnn",
        resolution=res,
        key_added=key,
        flavor="igraph",
        n_iterations=2,
        directed=False,
    )

    # Plot UMAP colorata per questo clustering
    fig, ax = plt.subplots(figsize=(6, 5))
    sc.pl.embedding(
        mdata,
        basis="X_wnn_umap",
        color=key,
        title=f"WNN UMAP — Leiden res={res}",
        frameon=False,
        ax=ax,
        show=False,
    )
    out_path = os.path.join(fig_dir, f"wnn_umap_leiden_res{res}.pdf")
    plt.savefig(out_path, dpi=300, bbox_inches="tight")
    plt.close(fig)
    print(f"[INFO] Salvato plot → {out_path}")

# (Opzionale) Plot per “modality” se esiste in mdata.obs
if "modality" in mdata.obs.columns:
    fig, ax = plt.subplots(figsize=(6, 5))
    sc.pl.embedding(
        mdata,
        basis="X_wnn_umap",
        color="modality",
        title="WNN UMAP — modality",
        frameon=False,
        ax=ax,
        show=False,
    )
    out_path = os.path.join(fig_dir, "wnn_umap_modality.pdf")
    plt.savefig(out_path, dpi=300, bbox_inches="tight")
    plt.close(fig)
    print(f"[INFO] Salvato plot → {out_path}")

# 3) Calcolo ARI (se è stata preparata la colonna true_label nel Blocco 7)
def _maybe_ari(obs, pred_col, label_col=None):
    if label_col is None or label_col not in obs.columns:
        return np.nan
    valid = obs[[label_col, pred_col]].dropna()
    if valid.empty:
        return np.nan
    return adjusted_rand_score(valid[label_col].astype(str), valid[pred_col].astype(str))

from sklearn.metrics import adjusted_rand_score

results = []
label_col = None
if "true_label_col" in globals() and true_label_col is not None:
    label_col = true_label_col
elif "true_label" in mdata.obs.columns:
    label_col = "true_label"

if label_col is not None:
    for res in wnn_res_list:
        col = f"leiden_wnn_{res}"
        ari = _maybe_ari(mdata.obs, col, label_col)
        results.append({"method": "WNN", "resolution": res, "ARI": float(ari)})
    res_df = pd.DataFrame(results).sort_values(["resolution"])
    display(res_df)
    csv_path = os.path.join(out_dir, "ARI_WNN_summary.csv")
    res_df.to_csv(csv_path, index=False)
    print(f"[INFO] ARI salvati → {csv_path}")
else:
    print("[WARN] Nessuna colonna di etichette vere trovata (true_label). Salto il calcolo ARI.")

# 4) Salva il MuData aggiornato
mdata.write(os.path.join(out_dir, "mdata_after_wnn.h5mu"))
print(f"[INFO] Salvato MuData → {os.path.join(out_dir, 'mdata_after_wnn.h5mu')}")

[INFO] Costruisco grafo multimodale WNN...[INFO] Calcolo UMAP su WNN...[INFO] Leiden WNN alle risoluzioni: [0.5, 1.0, 1.5, 2.0][INFO] Salvato plot → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/figures_wnn/wnn_umap_leiden_res0.5.pdf[INFO] Salvato plot → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/figures_wnn/wnn_umap_leiden_res1.0.pdf[INFO] Salvato plot → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/figures_wnn/wnn_umap_leiden_res1.5.pdf[INFO] Salvato plot → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/figures_wnn/wnn_umap_leiden_res2.0.pdf

method  resolution       ARI
0    WNN         0.5  0.264106
1    WNN         1.0  0.263178
2    WNN         1.5  0.271365
3    WNN         2.0  0.311895

[INFO] ARI salvati → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/ARI_WNN_summary.csv[INFO] Salvato MuData → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/mdata_after_wnn.h5mu

In [19]:
# --- BLOCCO 9: Integrazione concatenazione PCA (RNA+DNA) + Leiden + ARI (DEBUG 5×5 MODE) ---
import numpy as np
import pandas as pd
import scanpy as sc
import matplotlib.pyplot as plt
from sklearn.metrics import adjusted_rand_score
import os

concat_dir = os.path.join(out_dir, "concat_pca")
os.makedirs(concat_dir, exist_ok=True)
fig_dir = os.path.join(concat_dir, "figures_concat")
os.makedirs(fig_dir, exist_ok=True)

print("[INFO] Inizio integrazione per concatenazione PCA (DEBUG 5×5 MODE)...")

# === 1️⃣ RNA e DNA PCA check ===
for mod in ["rna", "dna"]:
    if "X_pca" not in mdata[mod].obsm:
        raise ValueError(f"[ERROR] Manca PCA per {mod}! Riesegui sc.tl.pca.")
    
    print(f"\n[DEBUG] --- {mod.upper()} ---")
    print(f"Shape (cells × features): {mdata[mod].shape}")

    # Prime 5×5 celle della matrice normalizzata
    X = mdata[mod].X
    block_raw = X[:5, :5].A if hasattr(X, "A") else np.asarray(X[:5, :5])
    print(f"Prime 5×5 celle {mod} (normalizzate e scalate):\n{np.round(block_raw, 4)}")

    # PCA info# PCA info
    X_pca = mdata[mod].obsm["X_pca"]
    print(f"PCA shape: {X_pca.shape}, varianza media: {np.var(X_pca):.4f}")

    # Mostra le prime 5 righe e 5 colonne della PCA
    print("Prime 5x5 celle della PCA:")
    print(np.round(X_pca[:5, :5], 4))

    # Varianza spiegata (se disponibile)
    if "pca" in mdata[mod].uns and "variance_ratio" in mdata[mod].uns["pca"]:
        vr = mdata[mod].uns["pca"]["variance_ratio"]
        print(f"PCA variance ratio (prime 5): {np.round(vr[:5], 4)}")
        
# === 2️⃣ Estrai PCA e concatena ===
pca_rna = mdata["rna"].obsm["X_pca"]
pca_dna = mdata["dna"].obsm["X_pca"]

if pca_rna.shape[0] != pca_dna.shape[0]:
    raise ValueError(f"[ERROR] RNA e DNA hanno celle diverse: RNA={pca_rna.shape[0]} DNA={pca_dna.shape[0]}")

print(f"\n[INFO] Celle allineate: {pca_rna.shape[0]}")
X_concat = np.concatenate([pca_rna, pca_dna], axis=1)
mdata.obsm["X_concat_pca"] = X_concat

print(f"[INFO] Concatenazione PCA completata: {X_concat.shape}")
print(f"[DEBUG] Prime 5×5 celle CONCATENATE:\n{np.round(X_concat[:5, :5], 4)}")

# === 3️⃣ Neighbors, UMAP, Leiden ===
sc.pp.neighbors(mdata, use_rep="X_concat_pca")
conn = mdata.obsp["connectivities"]
dist = mdata.obsp["distances"]
print(f"[DEBUG] Neighbors graph: shape={conn.shape}, mean_conn={conn.mean():.6f}, nnz={conn.nnz}")
print(f"[DEBUG] Neighbors graph: shape={dist.shape}, mean_conn={dist.mean():.6f}, nnz={dist.nnz}")


sc.tl.umap(mdata)
mdata.obsm["X_concat_umap"] = mdata.obsm["X_umap"].copy()

concat_res_list = [0.5, 1.0, 1.5, 2.0]
print(f"[INFO] Calcolo Leiden per risoluzioni: {concat_res_list}")

for res in concat_res_list:
    key = f"leiden_concat_{res:.2f}".rstrip("0").rstrip(".")
    sc.tl.leiden(
        mdata,
        resolution=res,
        key_added=key,
        flavor="igraph",
        n_iterations=2,
        directed=False,
        random_state=0,   # deterministic
    )

    # Debug cluster info
    n_clusters = mdata.obs[key].nunique()
    sizes = mdata.obs[key].value_counts().sort_index().values
    print(f"[DEBUG] → {key}: {n_clusters} clusters | mean={np.mean(sizes):.1f} | min={np.min(sizes)} | max={np.max(sizes)}")

    # UMAP plot
    fig, ax = plt.subplots(figsize=(6, 5))
    sc.pl.embedding(
        mdata,
        basis="X_concat_umap",
        color=key,
        title=f"Concat PCA UMAP — Leiden res={res}",
        frameon=False,
        ax=ax,
        show=False,
    )
    out_path = os.path.join(fig_dir, f"concat_umap_leiden_res{res}.pdf")
    plt.savefig(out_path, dpi=300, bbox_inches="tight")
    plt.close(fig)
    print(f"[INFO] Salvato → {out_path}")

# === 4️⃣ ARI (se presente true_label) ===
label_col = None
if "true_label_col" in globals() and true_label_col is not None:
    label_col = true_label_col
elif "true_label" in mdata.obs.columns:
    label_col = "true_label"

def _maybe_ari(obs, pred_col, label_col=None):
    if label_col is None or label_col not in obs.columns:
        return np.nan
    valid = obs[[label_col, pred_col]].dropna()
    if valid.empty:
        return np.nan
    return adjusted_rand_score(valid[label_col].astype(str), valid[pred_col].astype(str))

results_concat = []
if label_col is not None:
    for res in concat_res_list:
        col = f"leiden_concat_{res:.2f}".rstrip("0").rstrip(".")
        ari = _maybe_ari(mdata.obs, col, label_col)
        results_concat.append({"method": "ConcatPCA", "resolution": res, "ARI": float(ari)})
    df_concat = pd.DataFrame(results_concat).sort_values("resolution")
    print("\n=== RISULTATI ARI CONCAT (DEBUG 5×5) ===")
    print(df_concat.to_string(index=False))
    csv_path = os.path.join(concat_dir, "ARI_ConcatPCA_summary.csv")
    df_concat.to_csv(csv_path, index=False)
    print(f"[INFO] ARI salvati → {csv_path}")
else:
    print("[WARN] Nessuna colonna true_label trovata, salto ARI per Concat PCA.")

# === 5️⃣ Salvataggio MuData ===
out_path = os.path.join(concat_dir, "mdata_after_concat.h5mu")
mdata.write(out_path)
print(f"[INFO] Salvato MuData → {out_path}")

[INFO] Inizio integrazione per concatenazione PCA (DEBUG 5×5 MODE)...

[DEBUG] --- RNA ---
Shape (cells × features): (5000, 10000)
Prime 5×5 celle rna (normalizzate e scalate):
[[-4.5930e-01 -1.0819e+00  4.8890e-01 -3.9620e-01  1.5960e-01]
 [-1.0020e+00 -2.8540e-01 -1.4451e+00 -1.3384e+00 -3.0990e-01]
 [-5.4080e-01  1.1150e-01  1.3419e+00  9.8180e-01 -1.3718e+00]
 [ 1.0625e+00  1.9301e+00  1.1301e+00 -1.3384e+00  1.3454e+00]
 [-1.9660e-01 -8.3400e-02 -1.4451e+00 -1.3384e+00 -1.5000e-03]]
PCA shape: (5000, 50), varianza media: 51.6740
Prime 5x5 celle della PCA:
[[-36.2213  28.7004  16.1661  -0.816   -3.7326]
 [-36.9042  26.9355  16.6614  -1.1801   3.8297]
 [  1.8618  -3.6369 -18.9392  45.1308   1.4271]
 [  6.9455 -32.0362  35.4417  -1.3034  -1.8827]
 [-37.3183  28.8054  16.4231  -1.7821   5.1176]]
PCA variance ratio (prime 5): [0.0619 0.0602 0.0595 0.0569 0.0004]

[DEBUG] --- DNA ---
Shape (cells × features): (5000, 20000)
Prime 5×5 celle dna (normalizzate e scalate):
[[-0.4074 -0.3807 

In [20]:
# --- BLOCCO 10: Integrazione MOFA(+) + UMAP + Leiden + ARI ---

import os
import numpy as np
import pandas as pd
import scanpy as sc
import muon as mu
import matplotlib.pyplot as plt
from sklearn.metrics import adjusted_rand_score

mofa_dir = os.path.join(out_dir, "mofa")
os.makedirs(mofa_dir, exist_ok=True)
fig_dir = os.path.join(mofa_dir, "figures_mofa")
os.makedirs(fig_dir, exist_ok=True)

# 0️⃣ Verifica che mofapy2 sia installato
try:
    import mofapy2  # noqa: F401
except ImportError:
    raise ImportError("Devi installare mofapy2 prima di usare MOFA → pip install mofapy2")

# 1️⃣ Imposta likelihood per ciascuna vista
likelihoods = {}
for view in mdata.mod.keys():
    X = mdata.mod[view].X
    try:
        vals = np.unique(X.data if hasattr(X, "data") else np.asarray(X).ravel())
        is_binary = np.all(np.isin(vals, [0, 1]))
    except Exception:
        is_binary = False

    if view.lower() in ("rna", "gex", "gene", "transcriptome"):
        likelihoods[view] = "gaussian"
    elif is_binary:
        likelihoods[view] = "bernoulli"
    else:
        likelihoods[view] = "gaussian"

print("[INFO] Likelihood per vista:", likelihoods)

# ➕ Converti in LISTA nell'ordine delle viste in mdata.mod
likelihoods_list = [likelihoods[view] for view in mdata.mod.keys()]
print("[INFO] Likelihoods usate in ordine:", likelihoods_list)

# 2️⃣ Esegui MOFA
n_factors = 10
print(f"[INFO] Avvio MOFA con n_factors={n_factors}...")
mu.tl.mofa(
    mdata,
    n_factors=n_factors,
    likelihoods=likelihoods_list,  # ✅ usa lista, non dict
    convergence_mode="medium",
    seed=0,
)

# I fattori vengono salvati in mdata.obsm["X_mofa"]
assert "X_mofa" in mdata.obsm, "MOFA non ha prodotto X_mofa; controlla i log di mofapy2"

# 3️⃣ Costruisci grafo e UMAP nello spazio MOFA
print("[INFO] Calcolo neighbors e UMAP su fattori MOFA...")
sc.pp.neighbors(mdata, use_rep="X_mofa")
sc.tl.umap(mdata)
mdata.obsm["X_mofa_umap"] = mdata.obsm["X_umap"].copy()

# 4️⃣ Leiden multi-risoluzione
mofa_res_list = [0.5, 1.0, 1.5, 2.0]
print(f"[INFO] Calcolo Leiden per risoluzioni: {mofa_res_list}")
for res in mofa_res_list:
    key = f"leiden_mofa_{res}"
    sc.tl.leiden(
        mdata,
        resolution=res,
        key_added=key,
        flavor="igraph",
        n_iterations=2,
        directed=False,
    )

    # Plot
    fig, ax = plt.subplots(figsize=(6, 5))
    sc.pl.embedding(
        mdata,
        basis="X_mofa_umap",
        color=key,
        title=f"MOFA UMAP — Leiden res={res}",
        frameon=False,
        ax=ax,
        show=False,
    )
    out_path = os.path.join(fig_dir, f"mofa_umap_leiden_res{res}.pdf")
    plt.savefig(out_path, dpi=300, bbox_inches="tight")
    plt.close(fig)
    print(f"[INFO] Salvato → {out_path}")

# 5️⃣ Calcolo ARI (se esiste una colonna di verità)
def _maybe_ari(obs, pred_col, label_col=None):
    if label_col is None or label_col not in obs.columns:
        return np.nan
    valid = obs[[label_col, pred_col]].dropna()
    if valid.empty:
        return np.nan
    return adjusted_rand_score(valid[label_col].astype(str), valid[pred_col].astype(str))

label_col = None
if "true_label_col" in globals() and true_label_col is not None:
    label_col = true_label_col
elif "true_label" in mdata.obs.columns:
    label_col = "true_label"

results_mofa = []
if label_col is not None:
    for res in mofa_res_list:
        col = f"leiden_mofa_{res}"
        ari = _maybe_ari(mdata.obs, col, label_col)
        results_mofa.append({"method": "MOFA", "resolution": res, "ARI": float(ari)})
    df_mofa = pd.DataFrame(results_mofa).sort_values("resolution")
    display(df_mofa)
    csv_path = os.path.join(mofa_dir, "ARI_MOFA_summary.csv")
    df_mofa.to_csv(csv_path, index=False)
    print(f"[INFO] ARI salvati → {csv_path}")
else:
    print("[WARN] Nessuna colonna true_label trovata: salto ARI per MOFA.")

# 6️⃣ Salvataggio finale del MuData aggiornato
out_path = os.path.join(mofa_dir, "mdata_after_mofa.h5mu")
mdata.write(out_path)
print(f"[INFO] Salvato MuData finale → {out_path}")

[INFO] Likelihood per vista: {'rna': 'gaussian', 'dna': 'gaussian'}
[INFO] Likelihoods usate in ordine: ['gaussian', 'gaussian']
[INFO] Avvio MOFA con n_factors=10...

        #########################################################
        ###           __  __  ____  ______                    ### 
        ###          |  \/  |/ __ \|  ____/\    _             ### 
        ###          | \  / | |  | | |__ /  \ _| |_           ### 
        ###          | |\/| | |  | |  __/ /\ \_   _|          ###
        ###          | |  | | |__| | | / ____ \|_|            ###
        ###          |_|  |_|\____/|_|/_/    \_\              ###
        ###                                                   ### 
        ######################################################### 
       
 
        Loaded view='rna' group='group1' with N=5000 samples and D=10000 features...
Loaded view='dna' group='group1' with N=5000 samples and D=20000 features...

Model options:
- Automatic Relevance Determination prior on 

method  resolution       ARI
0   MOFA         0.5  0.569959
1   MOFA         1.0  0.569959
2   MOFA         1.5  0.569959
3   MOFA         2.0  0.420227

[INFO] ARI salvati → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/mofa/ARI_MOFA_summary.csv[INFO] Salvato MuData finale → ../tests/sim_c5000_g10000_v20000_ct5_gt4_es0.3_vs0.1_ee0.3_ve0.3_ln0.3/mofa/mdata_after_mofa.h5mu